In [3]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [4]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [5]:
# Convolutional neural network (two convolutional layers)
class LSTM_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(LSTM_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.rnn = nn.LSTM(64,256,dropout=0.25)
        self.fc1 = nn.Linear(256, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(256, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.rnn(x)
        #b,64,256
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,256 * b,64,1 = b,64,256
        x = torch.sum(x,dim=1)
        #b,64,256 -> b,,256
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [6]:
test = LSTM_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.25 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\functional.py:1795: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")


torch.Size([10, 4])

In [7]:
writer = SummaryWriter()

In [8]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [9]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [10]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [11]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [12]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [13]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [14]:
model = LSTM_AT(num_classes).to(device)

In [15]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [16]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 20.3125%, Training Loss: 1.5399%
Epoch [1/300], Step [2/225], Training Accuracy: 20.3125%, Training Loss: 1.5135%
Epoch [1/300], Step [3/225], Training Accuracy: 21.3542%, Training Loss: 1.5249%
Epoch [1/300], Step [4/225], Training Accuracy: 21.4844%, Training Loss: 1.5082%
Epoch [1/300], Step [5/225], Training Accuracy: 21.5625%, Training Loss: 1.4904%
Epoch [1/300], Step [6/225], Training Accuracy: 22.3958%, Training Loss: 1.4925%
Epoch [1/300], Step [7/225], Training Accuracy: 23.6607%, Training Loss: 1.4814%
Epoch [1/300], Step [8/225], Training Accuracy: 24.4141%, Training Loss: 1.4721%
Epoch [1/300], Step [9/225], Training Accuracy: 25.1736%, Training Loss: 1.4679%
Epoch [1/300], Step [10/225], Training Accuracy: 24.8438%, Training Loss: 1.4782%
Epoch [1/300], Step [11/225], Training Accuracy: 24.7159%, Training Loss: 1.4770%
Epoch [1/300], Step [12/225], Training Accuracy: 24.7396%, Training Loss: 1.4777%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [114/225], Training Accuracy: 28.9885%, Training Loss: 1.3988%
Epoch [1/300], Step [115/225], Training Accuracy: 29.0897%, Training Loss: 1.3985%
Epoch [1/300], Step [116/225], Training Accuracy: 29.1083%, Training Loss: 1.3980%
Epoch [1/300], Step [117/225], Training Accuracy: 29.0865%, Training Loss: 1.3980%
Epoch [1/300], Step [118/225], Training Accuracy: 29.0519%, Training Loss: 1.3978%
Epoch [1/300], Step [119/225], Training Accuracy: 29.0310%, Training Loss: 1.3978%
Epoch [1/300], Step [120/225], Training Accuracy: 29.0234%, Training Loss: 1.3977%
Epoch [1/300], Step [121/225], Training Accuracy: 29.0289%, Training Loss: 1.3972%
Epoch [1/300], Step [122/225], Training Accuracy: 29.0343%, Training Loss: 1.3969%
Epoch [1/300], Step [123/225], Training Accuracy: 28.9888%, Training Loss: 1.3970%
Epoch [1/300], Step [124/225], Training Accuracy: 29.0449%, Training Loss: 1.3971%
Epoch [1/300], Step [125/225], Training Accuracy: 28.9625%, Training Loss: 1.3975%
Epoc

Epoch [2/300], Step [3/225], Training Accuracy: 30.2083%, Training Loss: 1.3284%
Epoch [2/300], Step [4/225], Training Accuracy: 32.0312%, Training Loss: 1.3120%
Epoch [2/300], Step [5/225], Training Accuracy: 32.1875%, Training Loss: 1.3163%
Epoch [2/300], Step [6/225], Training Accuracy: 33.0729%, Training Loss: 1.3227%
Epoch [2/300], Step [7/225], Training Accuracy: 33.9286%, Training Loss: 1.3145%
Epoch [2/300], Step [8/225], Training Accuracy: 33.9844%, Training Loss: 1.3079%
Epoch [2/300], Step [9/225], Training Accuracy: 34.5486%, Training Loss: 1.3103%
Epoch [2/300], Step [10/225], Training Accuracy: 35.3125%, Training Loss: 1.3021%
Epoch [2/300], Step [11/225], Training Accuracy: 34.9432%, Training Loss: 1.3022%
Epoch [2/300], Step [12/225], Training Accuracy: 35.2865%, Training Loss: 1.3007%
Epoch [2/300], Step [13/225], Training Accuracy: 35.2163%, Training Loss: 1.3033%
Epoch [2/300], Step [14/225], Training Accuracy: 34.4866%, Training Loss: 1.3123%
Epoch [2/300], Step [15

Epoch [2/300], Step [113/225], Training Accuracy: 36.4768%, Training Loss: 1.2854%
Epoch [2/300], Step [114/225], Training Accuracy: 36.5406%, Training Loss: 1.2844%
Epoch [2/300], Step [115/225], Training Accuracy: 36.5217%, Training Loss: 1.2840%
Epoch [2/300], Step [116/225], Training Accuracy: 36.5706%, Training Loss: 1.2833%
Epoch [2/300], Step [117/225], Training Accuracy: 36.5652%, Training Loss: 1.2837%
Epoch [2/300], Step [118/225], Training Accuracy: 36.5466%, Training Loss: 1.2837%
Epoch [2/300], Step [119/225], Training Accuracy: 36.5284%, Training Loss: 1.2834%
Epoch [2/300], Step [120/225], Training Accuracy: 36.6016%, Training Loss: 1.2829%
Epoch [2/300], Step [121/225], Training Accuracy: 36.5573%, Training Loss: 1.2831%
Epoch [2/300], Step [122/225], Training Accuracy: 36.6163%, Training Loss: 1.2825%
Epoch [2/300], Step [123/225], Training Accuracy: 36.5981%, Training Loss: 1.2823%
Epoch [2/300], Step [124/225], Training Accuracy: 36.5927%, Training Loss: 1.2821%
Epoc

Epoch [2/300], Step [222/225], Training Accuracy: 37.5422%, Training Loss: 1.2661%
Epoch [2/300], Step [223/225], Training Accuracy: 37.5911%, Training Loss: 1.2661%
Epoch [2/300], Step [224/225], Training Accuracy: 37.6186%, Training Loss: 1.2660%
Epoch [2/300], Step [225/225], Training Accuracy: 37.6042%, Training Loss: 1.2662%
Epoch [3/300], Step [1/225], Training Accuracy: 50.0000%, Training Loss: 1.1704%
Epoch [3/300], Step [2/225], Training Accuracy: 42.1875%, Training Loss: 1.2333%
Epoch [3/300], Step [3/225], Training Accuracy: 38.5417%, Training Loss: 1.2570%
Epoch [3/300], Step [4/225], Training Accuracy: 39.4531%, Training Loss: 1.2560%
Epoch [3/300], Step [5/225], Training Accuracy: 40.9375%, Training Loss: 1.2490%
Epoch [3/300], Step [6/225], Training Accuracy: 39.8438%, Training Loss: 1.2645%
Epoch [3/300], Step [7/225], Training Accuracy: 39.7321%, Training Loss: 1.2624%
Epoch [3/300], Step [8/225], Training Accuracy: 41.2109%, Training Loss: 1.2527%
Epoch [3/300], Step 

...

Epoch [298/300], Step [222/225], Training Accuracy: 99.5988%, Training Loss: 0.0198%
Epoch [298/300], Step [223/225], Training Accuracy: 99.5936%, Training Loss: 0.0198%
Epoch [298/300], Step [224/225], Training Accuracy: 99.5954%, Training Loss: 0.0198%
Epoch [298/300], Step [225/225], Training Accuracy: 99.5970%, Training Loss: 0.0197%
Epoch [299/300], Step [1/225], Training Accuracy: 100.0000%, Training Loss: 0.0054%
Epoch [299/300], Step [2/225], Training Accuracy: 99.2188%, Training Loss: 0.0190%
Epoch [299/300], Step [3/225], Training Accuracy: 99.4792%, Training Loss: 0.0161%
Epoch [299/300], Step [4/225], Training Accuracy: 99.6094%, Training Loss: 0.0205%
Epoch [299/300], Step [5/225], Training Accuracy: 99.6875%, Training Loss: 0.0176%
Epoch [299/300], Step [6/225], Training Accuracy: 99.2188%, Training Loss: 0.0205%
Epoch [299/300], Step [7/225], Training Accuracy: 99.3304%, Training Loss: 0.0233%
Epoch [299/300], Step [8/225], Training Accuracy: 99.2188%, Training Loss: 0.0

Epoch [299/300], Step [105/225], Training Accuracy: 99.4345%, Training Loss: 0.0216%
Epoch [299/300], Step [106/225], Training Accuracy: 99.4399%, Training Loss: 0.0216%
Epoch [299/300], Step [107/225], Training Accuracy: 99.4451%, Training Loss: 0.0215%
Epoch [299/300], Step [108/225], Training Accuracy: 99.4502%, Training Loss: 0.0215%
Epoch [299/300], Step [109/225], Training Accuracy: 99.4553%, Training Loss: 0.0214%
Epoch [299/300], Step [110/225], Training Accuracy: 99.4602%, Training Loss: 0.0213%
Epoch [299/300], Step [111/225], Training Accuracy: 99.4651%, Training Loss: 0.0212%
Epoch [299/300], Step [112/225], Training Accuracy: 99.4699%, Training Loss: 0.0210%
Epoch [299/300], Step [113/225], Training Accuracy: 99.4746%, Training Loss: 0.0210%
Epoch [299/300], Step [114/225], Training Accuracy: 99.4792%, Training Loss: 0.0209%
Epoch [299/300], Step [115/225], Training Accuracy: 99.4837%, Training Loss: 0.0208%
Epoch [299/300], Step [116/225], Training Accuracy: 99.4881%, Tra

Epoch [299/300], Step [206/225], Training Accuracy: 99.4691%, Training Loss: 0.0213%
Epoch [299/300], Step [207/225], Training Accuracy: 99.4716%, Training Loss: 0.0212%
Epoch [299/300], Step [208/225], Training Accuracy: 99.4742%, Training Loss: 0.0212%
Epoch [299/300], Step [209/225], Training Accuracy: 99.4692%, Training Loss: 0.0213%
Epoch [299/300], Step [210/225], Training Accuracy: 99.4717%, Training Loss: 0.0212%
Epoch [299/300], Step [211/225], Training Accuracy: 99.4742%, Training Loss: 0.0212%
Epoch [299/300], Step [212/225], Training Accuracy: 99.4767%, Training Loss: 0.0212%
Epoch [299/300], Step [213/225], Training Accuracy: 99.4792%, Training Loss: 0.0212%
Epoch [299/300], Step [214/225], Training Accuracy: 99.4816%, Training Loss: 0.0211%
Epoch [299/300], Step [215/225], Training Accuracy: 99.4840%, Training Loss: 0.0211%
Epoch [299/300], Step [216/225], Training Accuracy: 99.4864%, Training Loss: 0.0210%
Epoch [299/300], Step [217/225], Training Accuracy: 99.4888%, Tra

Epoch [300/300], Step [83/225], Training Accuracy: 99.5482%, Training Loss: 0.0210%
Epoch [300/300], Step [84/225], Training Accuracy: 99.5536%, Training Loss: 0.0208%
Epoch [300/300], Step [85/225], Training Accuracy: 99.5404%, Training Loss: 0.0210%
Epoch [300/300], Step [86/225], Training Accuracy: 99.5458%, Training Loss: 0.0210%
Epoch [300/300], Step [87/225], Training Accuracy: 99.5510%, Training Loss: 0.0208%
Epoch [300/300], Step [88/225], Training Accuracy: 99.5561%, Training Loss: 0.0208%
Epoch [300/300], Step [89/225], Training Accuracy: 99.5611%, Training Loss: 0.0208%
Epoch [300/300], Step [90/225], Training Accuracy: 99.5486%, Training Loss: 0.0209%
Epoch [300/300], Step [91/225], Training Accuracy: 99.5536%, Training Loss: 0.0208%
Epoch [300/300], Step [92/225], Training Accuracy: 99.5414%, Training Loss: 0.0211%
Epoch [300/300], Step [93/225], Training Accuracy: 99.5464%, Training Loss: 0.0209%
Epoch [300/300], Step [94/225], Training Accuracy: 99.5346%, Training Loss: 

Epoch [300/300], Step [203/225], Training Accuracy: 99.5074%, Training Loss: 0.0214%
Epoch [300/300], Step [204/225], Training Accuracy: 99.5098%, Training Loss: 0.0213%
Epoch [300/300], Step [205/225], Training Accuracy: 99.5122%, Training Loss: 0.0213%
Epoch [300/300], Step [206/225], Training Accuracy: 99.5070%, Training Loss: 0.0214%
Epoch [300/300], Step [207/225], Training Accuracy: 99.5094%, Training Loss: 0.0213%
Epoch [300/300], Step [208/225], Training Accuracy: 99.5117%, Training Loss: 0.0212%
Epoch [300/300], Step [209/225], Training Accuracy: 99.5141%, Training Loss: 0.0212%
Epoch [300/300], Step [210/225], Training Accuracy: 99.5164%, Training Loss: 0.0212%
Epoch [300/300], Step [211/225], Training Accuracy: 99.5113%, Training Loss: 0.0212%
Epoch [300/300], Step [212/225], Training Accuracy: 99.5062%, Training Loss: 0.0212%
Epoch [300/300], Step [213/225], Training Accuracy: 99.5012%, Training Loss: 0.0213%
Epoch [300/300], Step [214/225], Training Accuracy: 99.5035%, Tra

In [17]:
from playsound import playsound
playsound(u"sound.mp3")

In [18]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 46.081156197887715 %
